In [3]:
import pandas as pd
import folium
from folium import Choropleth
from branca.colormap import LinearColormap

# URL of the Excel file on GitHub
url = 'python.xlsx'

# Read the Excel file from the GitHub URL
df = pd.read_excel(url)

# Drop rows with NaN values in the relevant columns
df = df.dropna(subset=['lat', 'lon', 'gasValue'])

# Display the first few rows to ensure it's loaded correctly and NaNs are removed
print(df.head())

# Define categories for gasValue
def categorize(value):
    if value <= 100:
        return '0-100'
    elif 100 < value <= 500:
        return '100-500'
    else:
        return 'Above 500'

# Define a color palette
color_palette = {
    '0-100': '#FFD580',  # Light orange
    '100-500': 'orange',
    'Above 500': 'red'
}

# Create a base map centered around the average latitude and longitude
m = folium.Map(location=[df['lat'].mean(), df['lon'].mean()], zoom_start=10)

# Function to add CircleMarkers to the map based on category
def add_circle_markers(df, category):
    for _, row in df[df['category'] == category].iterrows():
        folium.CircleMarker(
            location=[row['lat'], row['lon']],
            radius=2,
            color=color_palette[category],
            fill=True,
            fill_color=color_palette[category],
            fill_opacity=0.7
        ).add_to(m)

# Categorize the gas values
df['category'] = df['gasValue'].apply(categorize)

# Add CircleMarkers for each category in the desired order
add_circle_markers(df, '0-100')
add_circle_markers(df, '100-500')
add_circle_markers(df, 'Above 500')

# Add a legend to the map (for visual reference) with opaque background
legend_html = """
    <div style="
        position: fixed; 
        bottom: 50px; left: 50px; width: 150px; height: 150px; 
        border:2px solid grey; background-color:white;
        opacity:1; z-index:9999; font-size:14px;
        ">
        <b>Gas Value Categories</b><br>
        <i style="background:#FFD580; width:24px; height:24px; display:inline-block;"></i> 0-100<br>
        <i style="background:orange; width:24px; height:24px; display:inline-block;"></i> 100-500<br>
        <i style="background:red; width:24px; height:24px; display:inline-block;"></i> Above 500
    </div>
"""
m.get_root().html.add_child(folium.Element(legend_html))

# Save the map to an HTML file
m.save('circle_map.html')

# Display the map (optional, only works in Jupyter Notebooks or IPython environments)
m


   point ID            timestamp        lat hemisLat         lon hemisLon  \
0       1.0  29/07/2024 08:39:46  53.569325        N -113.379327        W   
1     229.0  29/07/2024 08:49:12  53.569330        N -113.379422        W   
2     470.0  29/07/2024 08:59:26  53.569317        N -113.379422        W   
3     472.0  29/07/2024 08:59:26  53.569317        N -113.379422        W   
4     474.0  29/07/2024 08:59:33  53.569321        N -113.379422        W   

   gasValue  satellites  hdop  azimuth  speed  code    description  gridCell  \
0       2.6         7.0   1.3      0.0   0.56  11.0  Mission Start       NaN   
1       2.9        12.0   0.6      0.0   0.19  11.0  Mission Start       NaN   
2       2.9        12.0   0.7      0.0   0.00  51.0  Pause - Start       NaN   
3       2.9        12.0   0.7      0.0   0.00  99.0    Mission End       NaN   
4       3.0        12.0   0.7      0.0   0.00  11.0  Mission Start       NaN   

   name  
0   NaN  
1   NaN  
2   NaN  
3   NaN  
4   Na

In [3]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager

# Set up Selenium to take a screenshot
options = webdriver.ChromeOptions()
options.add_argument('--headless')  # Run in headless mode
driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)

# Open the map HTML file
driver.get('file://path_to_your_directory/circle_map.html')

# Save the screenshot
driver.save_screenshot('circle_map.png')
driver.quit()


In [ ]:
import matplotlib.pyplot as plt
import matplotlib.patches as patches
from PIL import Image
import numpy as np

# Load the saved map image
map_image = Image.open('circle_map.png')

# Define A3 size in inches (for printing at 300 DPI: 11.7 x 16.5 inches)
a3_width_inch = 11.7
a3_height_inch = 16.5
dpi = 300

# Create a new figure with A3 size
fig, ax = plt.subplots(figsize=(a3_width_inch, a3_height_inch), dpi=dpi)

# Remove axes
ax.axis('off')

# Display the map image
ax.imshow(map_image, extent=[0, a3_width_inch, 0, a3_height_inch])

# Draw scale bar
scale_bar_length = 1  # 1 inch on the sheet
scale_bar_width = 0.05  # Width of the scale bar in inches
scale_bar_x = a3_width_inch - 2  # X position of the scale bar
scale_bar_y = 1  # Y position of the scale bar
scale_bar_color = 'black'

# Draw the scale bar
scale_bar = patches.Rectangle((scale_bar_x, scale_bar_y), scale_bar_length, scale_bar_width, linewidth=1, edgecolor=scale_bar_color, facecolor=scale_bar_color)
ax.add_patch(scale_bar)

# Add scale bar label
ax.text(scale_bar_x + scale_bar_length / 2, scale_bar_y - 0.1, '1 km', ha='center', va='center', fontsize=12, color='black')

# Draw north arrow
north_arrow_size = 0.5  # Size of the north arrow in inches
north_arrow_x = a3_width_inch - 1.5  # X position of the north arrow
north_arrow_y = a3_height_inch - 1.5  # Y position of the north arrow

# Add north arrow (using a triangle)
north_arrow = patches.Polygon(
    [[north_arrow_x, north_arrow_y], 
     [north_arrow_x + north_arrow_size / 2, north_arrow_y + north_arrow_size],
     [north_arrow_x - north_arrow_size / 2, north_arrow_y + north_arrow_size]],
    closed=True, edgecolor='black', facecolor='black'
)
ax.add_patch(north_arrow)

# Add grid lines
grid_spacing = 65 / 1000  # Convert 65m to kilometers
x_ticks = np.arange(0, a3_width_inch, grid_spacing)
y_ticks = np.arange(0, a3_height_inch, grid_spacing)
for x in x_ticks:
    ax.axvline(x=x, color='grey', linestyle='--', linewidth=0.5)
for y in y_ticks:
    ax.axhline(y=y, color='grey', linestyle='--', linewidth=0.5)

# Save the final A3 sheet to a file
plt.savefig('a3_sheet.png', bbox_inches='tight', pad_inches=0.1, dpi=dpi)

plt.show()
